In [3]:
######################################################
## WRITE YOUR CREDENTIALS FOR SAFECTORY TO RUN CODE ##
######################################################
email = ""        ##  
password = ""                               ## 
######################################################

import requests
from datetime import datetime
import collections
import pandas as pd
from datetime import datetime

cattleData = {}
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

def createSession():
    return requests.Session()

def login(session):
    login_url = "https://devtrack.safectory.com/api/session"
    login_data = {
        "email": email,
        "password": password
    }
    response = session.post(login_url, data=login_data)

    # Return the response for further processing
    return response

session = createSession()
loginResponse = login(session)

if loginResponse.status_code == 200:
    print("Login successful!")
    
    protected_url = "https://devtrack.safectory.com/api/devices"
    api_response = session.get(protected_url)
    
    if api_response.status_code == 200:
        print("Access to protected resource successful!")
        print(api_response.json()[0]["id"])
    
    url = "https://devtrack.safectory.com/api/reports/summary"
    params = {
        "deviceId": "177657162",
        #"deviceId": api_response.json()[0]["id"],
        "from": "2024-08-22T00:00:00.000Z",
        "to": "2024-08-22T02:00:00.000Z"
    }

    # Send the GET request with the parameters using the same session
    response = session.get(url, params=params)

    # Check if the request was successful
    if response.status_code == 200:
        print("Request successful!")
        print(response.json())
    else:
        print(f"Request failed with status code {response.status_code}")
        print(response.text)
    

    url = "https://devtrack.safectory.com/api/reports/route"

    # Define the parameters for the request
    params = {
        "deviceId": "177657162",  # List of device IDs or [0] for all devices
        "from": "2024-08-21T00:00:00.000Z",  # Start time in UTC format
        "to": "2024-08-21T02:00:00.000Z",    # End time in UTC format
        "filterSameLocation": False,
        "filterFlapping": False,
        "filterNonBeacon": False,
        "useServerTime": False,
        "includeNoRssiFilterDevices": False
    }

    # Headers
    headers = {
        "Accept": "application/json"
    }

    # Send the GET request with the parameters and headers
    response = session.get(url, headers=headers, params=params)

    # Check if the request was successful
    if response.status_code == 200:
        print("Request successful!")
        sorted_data = sorted(response.json(), key=lambda x: datetime.fromisoformat(x['serverTime'].replace('Z', '+00:00')))
        for x in sorted_data:
            #print(x["rssi"], x["serverTime"], x["beaconName"])
            # Ensure 'serverTime' exists and 'rssi' is not None
            if x["rssi"] is not None and x["serverTime"] not in cattleData:
                # Store the 'rssi' and 'beaconName' under the 'serverTime' key
                cattleData[x["serverTime"]] = {"rssi": x["rssi"], "beaconName": x["beaconName"]}
            elif x["rssi"] is not None and cattleData[x["serverTime"]]["rssi"] < x["rssi"]:
                # Update 'rssi' and 'beaconName' if new 'rssi' is greater
                cattleData[x["serverTime"]]["rssi"] = x["rssi"]
                cattleData[x["serverTime"]]["beaconName"] = x["beaconName"]
    else:
        print(f"Request failed with status code {response.status_code}")
        print(response.text)  # Print the response for debugging purposes

else:
    print(f"Login failed: {loginResponse.status_code}")
    print(loginResponse.text)

#for x in cattleData:
#    print(x, cattleData[x]["beaconName"])

df = pd.DataFrame(response.json())

df
#cattleData[x]["rssi"], 

Login successful!
Access to protected resource successful!
162072586
Request successful!
[{'deviceId': 177657162, 'positionCount': 1.0, 'beaconCount': 0, 'deviceName': 'Multitag_V2_07_2C:A7:74:A1:2F:00', 'distance': 0.0, 'averageSpeed': 0.0, 'maxSpeed': 0.0, 'spentFuel': 0.0, 'startOdometer': 0.0, 'endOdometer': 0.0, 'engineHours': 0}]
Request successful!
2024-08-21T00:00:13.271+00:00 W10T_A7H_B-1-19 Tränke
2024-08-21T00:00:22.607+00:00 W10T_A7H_B-1-7
2024-08-21T00:00:49.562+00:00 W10T_A7H_B-1-7
2024-08-21T00:00:54.672+00:00 W10T_A7H_B-1-19 Tränke
2024-08-21T00:00:59.210+00:00 W10T_A7H_B-1-7
2024-08-21T00:01:08.372+00:00 W10T_A7H_B-1-7
2024-08-21T00:01:25.502+00:00 W10T_A7H_B-1-19 Tränke
2024-08-21T00:01:35.770+00:00 W10T_A7H_B-1-19 Tränke
2024-08-21T00:01:46.690+00:00 W10T_A7H_B-1-2
2024-08-21T00:01:52.707+00:00 W10T_A7H_B-1-6
2024-08-21T00:02:01.877+00:00 SF:00:00:00:00:00:DE
2024-08-21T00:02:12.826+00:00 W10T_A7H_B-1-11
2024-08-21T00:02:19.868+00:00 W10T_A7H_B-1-19 Tränke
2024-08-21

In [7]:
import pandas as pd
from datetime import datetime

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
# Function to format the serverTime
def format_server_time(server_time):
    # Parse the server time string and remove milliseconds and timezone
    return datetime.fromisoformat(server_time.replace('Z', '+00:00')).strftime('%Y-%m-%d %H:%M:%S')

# Convert cattleData to a list of dictionaries, formatting the serverTime
data = [{"serverTime": format_server_time(time), "beaconName": cattleData[time]["beaconName"]} for time in cattleData]

# Convert to a pandas DataFrame
df = pd.DataFrame(data)

df

serverTime                        beaconName
0     2024-08-21 00:00:13            W10T_A7H_B-1-19 Tränke
1     2024-08-21 00:00:22                    W10T_A7H_B-1-7
2     2024-08-21 00:00:49                    W10T_A7H_B-1-7
3     2024-08-21 00:00:54            W10T_A7H_B-1-19 Tränke
4     2024-08-21 00:00:59                    W10T_A7H_B-1-7
5     2024-08-21 00:01:08                    W10T_A7H_B-1-7
6     2024-08-21 00:01:25            W10T_A7H_B-1-19 Tränke
7     2024-08-21 00:01:35            W10T_A7H_B-1-19 Tränke
8     2024-08-21 00:01:46                    W10T_A7H_B-1-2
9     2024-08-21 00:01:52                    W10T_A7H_B-1-6
10    2024-08-21 00:02:01              SF:00:00:00:00:00:DE
11    2024-08-21 00:02:12                   W10T_A7H_B-1-11
12    2024-08-21 00:02:19            W10T_A7H_B-1-19 Tränke
13    2024-08-21 00:02:38                    W10T_A7H_B-1-2
14    2024-08-21 00:02:46                    W10T_A7H_B-1-1
15    2024-08-21 00:02:55                    W10T_A7H_B-1-1
16    2024-08-21 00:03:15                    W10T_A7H_B-1-2
17    2024-08-21 00:03:25                    W10T_A7H_B-1-2
18    2024-08-21 00:03:32            W10T_A7H_B-1-19 Tränke
19    2024-08-21 00:03:45                    W10T_A7H_B-1-2
20    2024-08-21 00:03:50            W10T_A7H_B-1-19 Tränke
21    2024-08-21 00:04:00            W10T_A7H_B-1-19 Tränke
22    2024-08-21 00:04:07            W10T_A7H_B-1-19 Tränke
23    2024-08-21 00:04:17            W10T_A7H_B-1-19 Tränke
24    2024-08-21 00:04:26            W10T_A7H_B-1-19 Tränke
25    2024-08-21 00:04:35            W10T_A7H_B-1-19 Tränke
26    2024-08-21 00:04:50                    W10T_A7H_B-1-2
27    2024-08-21 00:04:54                    W10T_A7H_B-1-7
28    2024-08-21 00:05:03            W10T_A7H_B-1-19 Tränke
29    2024-08-21 00:05:11            W10T_A7H_B-1-19 Tränke
30    2024-08-21 00:05:26            W10T_A7H_B-1-19 Tränke
31    2024-08-21 00:05:29            W10T_A7H_B-1-19 Tränke
32    2024-08-21 00:05:38            W10T_A7H_B-1-19 Tränke
33    2024-08-21 00:05:47                    W10T_A7H_B-1-2
34    2024-08-21 00:05:56                    W10T_A7H_B-1-7
35    2024-08-21 00:06:05                    W10T_A7H_B-1-2
36    2024-08-21 00:06:14                    W10T_A7H_B-1-2
37    2024-08-21 00:06:23                    W10T_A7H_B-1-2
38    2024-08-21 00:06:33                    W10T_A7H_B-1-2
39    2024-08-21 00:06:48                    W10T_A7H_B-1-6
40    2024-08-21 00:06:50            W10T_A7H_B-1-19 Tränke
41    2024-08-21 00:06:59            W10T_A7H_B-1-19 Tränke
42    2024-08-21 00:07:08            W10T_A7H_B-1-19 Tränke
43    2024-08-21 00:07:18                    W10T_A7H_B-1-6
44    2024-08-21 00:07:26                    W10T_A7H_B-1-2
45    2024-08-21 00:07:35                    W10T_A7H_B-1-6
46    2024-08-21 00:07:45            W10T_A7H_B-1-19 Tränke
47    2024-08-21 00:07:55            W10T_A7H_B-1-19 Tränke
48    2024-08-21 00:08:03            W10T_A7H_B-1-19 Tränke
49    2024-08-21 00:08:12                    W10T_A7H_B-1-1
50    2024-08-21 00:08:28            W10T_A7H_B-1-19 Tränke
51    2024-08-21 00:08:32              SF:00:00:00:00:00:DE
52    2024-08-21 00:08:39            W10T_A7H_B-1-19 Tränke
53    2024-08-21 00:08:48            W10T_A7H_B-1-19 Tränke
54    2024-08-21 00:08:59                    W10T_A7H_B-1-2
55    2024-08-21 00:09:07                    W10T_A7H_B-1-7
56    2024-08-21 00:09:15                    W10T_A7H_B-1-7
57    2024-08-21 00:09:26            W10T_A7H_B-1-19 Tränke
58    2024-08-21 00:09:33            W10T_A7H_B-1-19 Tränke
59    2024-08-21 00:09:45                    W10T_A7H_B-1-2
60    2024-08-21 00:09:51            W10T_A7H_B-1-19 Tränke
61    2024-08-21 00:10:03            W10T_A7H_B-1-19 Tränke
62    2024-08-21 00:10:11            W10T_A7H_B-1-19 Tränke
63    2024-08-21 00:10:18                    W10T_A7H_B-1-7
64    2024-08-21 00:10:31                    W10T_A7H_B-1-6
65    2024-08-21 00:10:48              SF:00:00:00:00:0

In [8]:
import pandas as pd

df = pd.DataFrame(data)
df['serverTime'] = pd.to_datetime(df['serverTime'])

# Create the 'end_time' column by shifting the 'serverTime' up by one row
df['end_time'] = df['serverTime'].shift(-1)
df['beaconName'] = df['beaconName'].shift(-1)

# Create a new DataFrame with the necessary columns
summary_df = df[['serverTime', 'end_time', 'beaconName']].copy()
summary_df.columns = ['start_time', 'end_time', 'beacon']

# Optionally, remove the last row if 'end_time' is NaN
summary_df = summary_df.dropna(subset=['end_time'])

summary_df

start_time            end_time                            beacon
0    2024-08-21 00:00:13 2024-08-21 00:00:22                    W10T_A7H_B-1-7
1    2024-08-21 00:00:22 2024-08-21 00:00:49                    W10T_A7H_B-1-7
2    2024-08-21 00:00:49 2024-08-21 00:00:54            W10T_A7H_B-1-19 Tränke
3    2024-08-21 00:00:54 2024-08-21 00:00:59                    W10T_A7H_B-1-7
4    2024-08-21 00:00:59 2024-08-21 00:01:08                    W10T_A7H_B-1-7
5    2024-08-21 00:01:08 2024-08-21 00:01:25            W10T_A7H_B-1-19 Tränke
6    2024-08-21 00:01:25 2024-08-21 00:01:35            W10T_A7H_B-1-19 Tränke
7    2024-08-21 00:01:35 2024-08-21 00:01:46                    W10T_A7H_B-1-2
8    2024-08-21 00:01:46 2024-08-21 00:01:52                    W10T_A7H_B-1-6
9    2024-08-21 00:01:52 2024-08-21 00:02:01              SF:00:00:00:00:00:DE
10   2024-08-21 00:02:01 2024-08-21 00:02:12                   W10T_A7H_B-1-11
11   2024-08-21 00:02:12 2024-08-21 00:02:19            W10T_A7H_B-1-19 Tränke
12   2024-08-21 00:02:19 2024-08-21 00:02:38                    W10T_A7H_B-1-2
13   2024-08-21 00:02:38 2024-08-21 00:02:46                    W10T_A7H_B-1-1
14   2024-08-21 00:02:46 2024-08-21 00:02:55                    W10T_A7H_B-1-1
15   2024-08-21 00:02:55 2024-08-21 00:03:15                    W10T_A7H_B-1-2
16   2024-08-21 00:03:15 2024-08-21 00:03:25                    W10T_A7H_B-1-2
17   2024-08-21 00:03:25 2024-08-21 00:03:32            W10T_A7H_B-1-19 Tränke
18   2024-08-21 00:03:32 2024-08-21 00:03:45                    W10T_A7H_B-1-2
19   2024-08-21 00:03:45 2024-08-21 00:03:50            W10T_A7H_B-1-19 Tränke
20   2024-08-21 00:03:50 2024-08-21 00:04:00            W10T_A7H_B-1-19 Tränke
21   2024-08-21 00:04:00 2024-08-21 00:04:07            W10T_A7H_B-1-19 Tränke
22   2024-08-21 00:04:07 2024-08-21 00:04:17            W10T_A7H_B-1-19 Tränke
23   2024-08-21 00:04:17 2024-08-21 00:04:26            W10T_A7H_B-1-19 Tränke
24   2024-08-21 00:04:26 2024-08-21 00:04:35            W10T_A7H_B-1-19 Tränke
25   2024-08-21 00:04:35 2024-08-21 00:04:50                    W10T_A7H_B-1-2
26   2024-08-21 00:04:50 2024-08-21 00:04:54                    W10T_A7H_B-1-7
27   2024-08-21 00:04:54 2024-08-21 00:05:03            W10T_A7H_B-1-19 Tränke
28   2024-08-21 00:05:03 2024-08-21 00:05:11            W10T_A7H_B-1-19 Tränke
29   2024-08-21 00:05:11 2024-08-21 00:05:26            W10T_A7H_B-1-19 Tränke
30   2024-08-21 00:05:26 2024-08-21 00:05:29            W10T_A7H_B-1-19 Tränke
31   2024-08-21 00:05:29 2024-08-21 00:05:38            W10T_A7H_B-1-19 Tränke
32   2024-08-21 00:05:38 2024-08-21 00:05:47                    W10T_A7H_B-1-2
33   2024-08-21 00:05:47 2024-08-21 00:05:56                    W10T_A7H_B-1-7
34   2024-08-21 00:05:56 2024-08-21 00:06:05                    W10T_A7H_B-1-2
35   2024-08-21 00:06:05 2024-08-21 00:06:14                    W10T_A7H_B-1-2
36   2024-08-21 00:06:14 2024-08-21 00:06:23                    W10T_A7H_B-1-2
37   2024-08-21 00:06:23 2024-08-21 00:06:33                    W10T_A7H_B-1-2
38   2024-08-21 00:06:33 2024-08-21 00:06:48                    W10T_A7H_B-1-6
39   2024-08-21 00:06:48 2024-08-21 00:06:50            W10T_A7H_B-1-19 Tränke
40   2024-08-21 00:06:50 2024-08-21 00:06:59            W10T_A7H_B-1-19 Tränke
41   2024-08-21 00:06:59 2024-08-21 00:07:08            W10T_A7H_B-1-19 Tränke
42   2024-08-21 00:07:08 2024-08-21 00:07:18                    W10T_A7H_B-1-6
43   2024-08-21 00:07:18 2024-08-21 00:07:26                    W10T_A7H_B-1-2
44   2024-08-21 00:07:26 2024-08-21 00:07:35                    W10T_A7H_B-1-6
45   2024-08-21 00:07:35 2024-08-21 00:07:45            W10T_A7H_B-1-19 Tränke
46   2024-08-21 00:07:45 2024-08-21 00:07:55            W10T_A7H_B-1-19 Tränke
47   2024-08-21 00:07:55 2024-08-21 00:08:03            W10T_A7H_B-1-19 Tränke
48   2024-08-21 00:08:03 2024-08-21 00:08:12                    W10T_A7H_B-1-1
49   2024-08-21 00:08:12 2024-08-21 00:08:28            W10T_A7H

In [9]:
# Detect changes in the beacon to create a group identifier
summary_df['group'] = (summary_df['beacon'] != summary_df['beacon'].shift()).cumsum()

# Group by the created 'group' identifier to combine consecutive entries
merged_df = summary_df.groupby('group').agg(
    start_time=('start_time', 'first'),
    end_time=('end_time', 'last'),
    beacon=('beacon', 'first')  # Ensure the beacon name is retained after grouping
).reset_index(drop=True)

# Calculate the time difference in seconds
merged_df['duration'] = (merged_df['end_time'] - merged_df['start_time']).dt.total_seconds()

# Define the behavior based on conditions
merged_df['behavior'] = merged_df.apply(
    lambda row: 'Drinking' if 'Tränke' in row['beacon'] and row['duration'] >= 61 else '',
    axis=1
)

merged_df

start_time            end_time  \
0    2024-08-21 00:00:13 2024-08-21 00:00:49   
1    2024-08-21 00:00:49 2024-08-21 00:00:54   
2    2024-08-21 00:00:54 2024-08-21 00:01:08   
3    2024-08-21 00:01:08 2024-08-21 00:01:35   
4    2024-08-21 00:01:35 2024-08-21 00:01:46   
5    2024-08-21 00:01:46 2024-08-21 00:01:52   
6    2024-08-21 00:01:52 2024-08-21 00:02:01   
7    2024-08-21 00:02:01 2024-08-21 00:02:12   
8    2024-08-21 00:02:12 2024-08-21 00:02:19   
9    2024-08-21 00:02:19 2024-08-21 00:02:38   
10   2024-08-21 00:02:38 2024-08-21 00:02:55   
11   2024-08-21 00:02:55 2024-08-21 00:03:25   
12   2024-08-21 00:03:25 2024-08-21 00:03:32   
13   2024-08-21 00:03:32 2024-08-21 00:03:45   
14   2024-08-21 00:03:45 2024-08-21 00:04:35   
15   2024-08-21 00:04:35 2024-08-21 00:04:50   
16   2024-08-21 00:04:50 2024-08-21 00:04:54   
17   2024-08-21 00:04:54 2024-08-21 00:05:38   
18   2024-08-21 00:05:38 2024-08-21 00:05:47   
19   2024-08-21 00:05:47 2024-08-21 00:05:56   
20   2024-08-21 00:05:56 2024-08-21 00:06:33   
21   2024-08-21 00:06:33 2024-08-21 00:06:48   
22   2024-08-21 00:06:48 2024-08-21 00:07:08   
23   2024-08-21 00:07:08 2024-08-21 00:07:18   
24   2024-08-21 00:07:18 2024-08-21 00:07:26   
25   2024-08-21 00:07:26 2024-08-21 00:07:35   
26   2024-08-21 00:07:35 2024-08-21 00:08:03   
27   2024-08-21 00:08:03 2024-08-21 00:08:12   
28   2024-08-21 00:08:12 2024-08-21 00:08:28   
29   2024-08-21 00:08:28 2024-08-21 00:08:32   
30   2024-08-21 00:08:32 2024-08-21 00:08:48   
31   2024-08-21 00:08:48 2024-08-21 00:08:59   
32   2024-08-21 00:08:59 2024-08-21 00:09:15   
33   2024-08-21 00:09:15 2024-08-21 00:09:33   
34   2024-08-21 00:09:33 2024-08-21 00:09:45   
35   2024-08-21 00:09:45 2024-08-21 00:10:11   
36   2024-08-21 00:10:11 2024-08-21 00:10:18   
37   2024-08-21 00:10:18 2024-08-21 00:10:31   
38   2024-08-21 00:10:31 2024-08-21 00:10:48   
39   2024-08-21 00:10:48 2024-08-21 00:10:59   
40   2024-08-21 00:10:59 2024-08-21 00:11:04   
41   2024-08-21 00:11:04 2024-08-21 00:11:12   
42   2024-08-21 00:11:12 2024-08-21 00:11:21   
43   2024-08-21 00:11:21 2024-08-21 00:11:31   
44   2024-08-21 00:11:31 2024-08-21 00:11:39   
45   2024-08-21 00:11:39 2024-08-21 00:11:48   
46   2024-08-21 00:11:48 2024-08-21 00:11:57   
47   2024-08-21 00:11:57 2024-08-21 00:12:06   
48   2024-08-21 00:12:06 2024-08-21 00:12:20   
49   2024-08-21 00:12:20 2024-08-21 00:12:26   
50   2024-08-21 00:12:26 2024-08-21 00:12:34   
51   2024-08-21 00:12:34 2024-08-21 00:12:44   
52   2024-08-21 00:12:44 2024-08-21 00:13:02   
53   2024-08-21 00:13:02 2024-08-21 00:13:42   
54   2024-08-21 00:13:42 2024-08-21 00:14:05   
55   2024-08-21 00:14:05 2024-08-21 00:14:16   
56   2024-08-21 00:14:16 2024-08-21 00:14:28   
57   2024-08-21 00:14:28 2024-08-21 00:15:13   
58   2024-08-21 00:15:13 2024-08-21 00:15:18   
59   2024-08-21 00:15:18 2024-08-21 00:15:26   
60   2024-08-21 00:15:26 2024-08-21 00:15:46   
61   2024-08-21 00:15:46 2024-08-21 00:16:07   
62   2024-08-21 00:16:07 2024-08-21 00:16:23   
63   2024-08-21 00:16:23 2024-08-21 00:16:38   
64   2024-08-21 00:16:38 2024-08-21 00:16:47   
65   2024-08-21 00:16:47 2024-08-21 00:17:05   
66   2024-08-21 00:17:05 2024-08-21 00:17:15   
67   2024-08-21 00:17:15 2024-08-21 00:17:22   
68   2024-08-21 00:17:22 2024-08-21 00:17:33   
69   2024-08-21 00:17:33 2024-08-21 00:17:50   
70   2024-08-21 00:17:50 2024-08-21 00:18:00   
71   2024-08-21 00:18:00 2024-08-21 00:18:08   
72   2024-08-21 00:18:08 2024-08-21 00:18:16   
73   2024-08-21 00:18:16 2024-08-21 00:18:29   
74   2024-08-21 00:18:29 2024-08-21 00:18:36   
75   2024-08-21 00:18:36 2024-08-21 00:18:45   
76   2024-08-21 00:18:45 2024-08-21 00:18:53   
77   2024-08-21 00:18:53 2024-08-21 00:19:08   
78   2024-08-21 00:19:08 2024-08-21 00:19:11   
79   2024-08-21 00:19:11 2024-08-21 00:19:22   
80   2024-08-21 00:19:22 2024-08-21 00:19:29   
81   2024-08-21 00:19:29 2024-08-21 00:19:38   
82   2024-08-21 00:19:38 2024-